<a href="https://colab.research.google.com/github/FMazzoni/StreetSigns/blob/main/BostonStreetSigns.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Import and Config

In [1]:
# Install packages to colab environment 
# !sudo apt-get update && apt-get install -y libspatialindex-dev
# !pip install rtree
!pip install plotly
!pip install geopandas
# !pip install OSMPythonTools
!pip install osmnx 

     |████████████████████████████████| 1.0MB 25.5MB/s 
     |████████████████████████████████| 15.3MB 245kB/s 
     |████████████████████████████████| 6.6MB 29.0MB/s 
     |████████████████████████████████| 92kB 8.8MB/s 
  Found existing installation: click 8.0.0
    Uninstalling click-8.0.0:
      Successfully uninstalled click-8.0.0
     |████████████████████████████████| 102kB 9.6MB/s 
     |████████████████████████████████| 10.3MB 32.3MB/s 
     |████████████████████████████████| 61kB 6.7MB/s 
     |████████████████████████████████| 1.0MB 26.4MB/s 
ERROR: google-colab 1.0.0 has requirement requests~=2.23.0, but you'll have requests 2.25.1 which is incompatible.
ERROR: datascience 0.10.6 has requirement folium==0.2.1, but you'll have folium 0.8.3 which is incompatible.
ERROR: albumentations 0.1.12 has requirement imgaug<0.2.7,>=0.2.5, but you'll have imgaug 0.2.9 which is incompatible.
  Found existing installation: matplotlib 3.2.2
    Uninstalling matplotlib-3.2.2:
      Successf

In [2]:
import warnings 
warnings.filterwarnings('ignore')

import osmnx as ox
import numpy as np
import matplotlib.pyplot as plt
# %matplotlib inline
#import spatial analytics library
import plotly.express as px
import shapely.geometry

import pandas as pd  
import geopandas as gpd  # combines the capabilities of pandas and shapely for geospatial operations
# from shapely.geometry import Point, Polygon, MultiPolygon  # for manipulating text data into geospatial shapes
# from shapely import wkt  # stands for "well known text," allows for interchange across GIS programs
# import rtree  # supports geospatial join


pd.set_option('display.max_columns', None)  # visualize all columns in dataframe

# Plotly and OSMNx Mapping

In [3]:
place_name = "Boston, Massachusetts, USA"

graph = ox.graph_from_place(place_name) #Does take some time to collect the data (especially with big cities)

type(graph)

networkx.classes.multidigraph.MultiDiGraph

In [4]:
area = ox.geocode_to_gdf (place_name)
# buildings = ox.geometries.geometries_from_place(place_name, tags = {'building': True})
nodes, edges = ox.graph_to_gdfs(graph)

## Functions

In [5]:
def plotly_read(df):
  geo_df = df
  lats = []
  lons = []
  names = []

  for feature, name, highway in zip(geo_df.geometry, geo_df.name, geo_df.highway):
      # print(highway)
      if isinstance(feature, shapely.geometry.linestring.LineString):
          linestrings = [feature]
      elif isinstance(feature, shapely.geometry.multilinestring.MultiLineString):
          linestrings = feature.geoms
      else:
          continue
      for linestring in linestrings:
          # print(name)
          x, y = linestring.xy
          lats = np.append(lats, y)
          lons = np.append(lons, x)
          if type(name) == str:
            names = np.append(names, [name]*len(y))
          elif type(highway) == list:
            name = highway[0]
            names = np.append(names, [name]*len(y))
          else:
            name = highway
            names = np.append(names, [name]*len(y))

          lats = np.append(lats, None)
          lons = np.append(lons, None)
          names = np.append(names, None)
  return lats, lons, names, df.reset_index().u, df.reset_index().v

## Getting Relevant Streets

In [6]:
# All highway names
all_highways = list(set(np.hstack(edges.highway)))
# Only Relevant Highway Types
rel_highways = [
 'residential',
 'secondary',
 'tertiary',
 'unclassified'
]

#Edges and Nodes data should already be collected
#Creating the mask for relavant highways
masks = np.zeros(len(edges.highway), dtype= bool)
for rel_highway in rel_highways:
  mask = [(rel_highway in highway) for highway in edges.highway]
  masks += mask

# Convert to arrays
osmid_u = edges[masks].reset_index().u.to_numpy()
osmid_v = edges[masks].reset_index().v.to_numpy()
osmid_nodes = nodes.index.to_numpy()


# Mask for edge element in node array 
new_mask = []

#Dont, all of OSMID_u is in OSMID_nodes just repeated
for x in osmid_nodes:
  if (x in osmid_u) == True:
    new_mask.append(True)
  else:
    new_mask.append(False)
    # print(x)

print(np.sum(new_mask))

19635


In [7]:
rel_nodes = []
rel_names = []
edge_masked = edges[masks].reset_index()

for i in osmid_nodes[new_mask]:
  u_mask = (edge_masked.u == i).to_numpy()
  v_mask = (edge_masked.v == i).to_numpy()
  try:
    names_in_node_u = set(np.hstack(edge_masked[u_mask].name.to_numpy()))
  except:
    names_in_node_u = [] 
  
  try:
    names_in_node_v = set(np.hstack(edge_masked[v_mask].name.to_numpy()))
  except:
    names_in_node_v = [] 
    
  

  if len(names_in_node_u) >= len(names_in_node_v) and len(names_in_node_u) >1:
    rel_nodes.append(i)
    rel_names.append(list(names_in_node_u))
  elif len(names_in_node_v) > len(names_in_node_u) and len(names_in_node_v) >1:
    rel_nodes.append(i)
    rel_names.append(list(names_in_node_v))



print('# of Intersections: ', len(rel_nodes) , ' # of Unique Streets: ', len(set(np.hstack(rel_names)) ) )

# of Intersections:  8221  # of Unique Streets:  3976


In [8]:
intersection_mask = np.zeros(len(osmid_nodes[new_mask] ), dtype = bool)

for i in rel_nodes:
  intersection_mask += (osmid_nodes[new_mask] == i)

intersections = nodes[new_mask][intersection_mask]

intersections.insert(0,"Intersecting Streets",rel_names)
intersections

Intersecting Streets          y  \
osmid                                                                      
30730954                                           [nan, nan]  42.367608   
30730955                                           [nan, nan]  42.367523   
61178875    [Washington Street, Crescent Street, Cambridge...  42.382149   
61339242                  [Chase Street, East Cottage Street]  42.318850   
61339246                   [East Cottage Street, Pond Street]  42.318674   
...                                                       ...        ...   
8733015070                   [Lomasney Way, Staniford Street]  42.364316   
8741453309                       [North Street, Union Street]  42.360377   
8741453602                    [North Street, Congress Street]  42.360320   
8741453603                    [North Street, Congress Street]  42.360238   
8759344915                    [Greenleaf Street, Leon Street]  42.338443   

                    x  street_count highway  ref                    geometry  
osmid                                                                         
30730954   -71.021817             3     NaN  NaN  POINT (-71.02182 42.36761)  
30730955   -71.021849             3     NaN  NaN  POINT (-71.02185 42.36752)  
61178875   -71.080878             4     NaN  NaN  POINT (-71.08088 42.38215)  
61339242   -71.059576             3     NaN  NaN  POINT (-71.05958 42.31885)  
61339246   -71.058839             4     NaN  NaN  POINT (-71.05884 42.31867)  
...               ...           ...     ...  ...                         ...  
8733015070 -71.063412             4     NaN  NaN  POINT (-71.06341 42.36432)  
8741453309 -71.056737             4     NaN  NaN  POINT (-71.05674 42.36038)  
8741453602 -71.057163             4     NaN  NaN  POINT (-71.05716 42.36032)  
8741453603 -71.057140             4     NaN  NaN  POINT (-71.05714 42.36024)  
8759344915 -71.090104             4     NaN  NaN  POINT (-71.09010 42.33844)  

[8221 rows x 7 columns]

In [9]:
lats, lons, names, df_u, df_v = plotly_read(edges[masks])

fig = px.line_mapbox(lat=lats, lon=lons, hover_name=names, mapbox_style="open-street-map")

fig.add_scattermapbox(lat =intersections.y, lon=  intersections.x, hovertext= rel_names)

fig.show()

In [10]:
unq_streets = np.unique(np.hstack(rel_names))

number_of_signs = []

for street in unq_streets:
    n_intersections = np.sum(np.hstack(rel_names) == street)
    number_of_signs.append(n_intersections)

In [11]:
d = {
    "Street Name" : unq_streets,
     "# of Signs To Buy": number_of_signs
}

signs_to_buy = pd.DataFrame( d )

print('Total Signs to Buy (Min):' ,np.sum(signs_to_buy['# of Signs To Buy']))

signs_to_buy

Total Signs to Buy (Min): 17145


Street Name  # of Signs To Buy
0              A Street                 24
1          Abbot Street                  1
2     Abbotsford Street                  3
3             Abby Road                  1
4       Aberdeen Street                  2
...                 ...                ...
3971       Zamora Court                  1
3972      Zamora Street                  3
3973     Zeigler Street                 11
3974      Zeller Street                  1
3975                nan                858

[3976 rows x 2 columns]

Total Estimated Cost of Sign Installation: \$1,028,700 (Assuming \$60 per Sign)

This of course isn't spent annually and only a rough estimate if one were to change out all the street signs in Boston all at once.

# Extra

In [ ]:
from shapely.geometry import LineString
from math import radians, cos, sin, asin, sqrt

# Calculates distance between 2 GPS coordinates
def haversine(lat1, lon1, lat2, lon2):
    """
    Calculate the great circle distance between two points 
    on the earth (specified in decimal degrees)
    """
    # convert decimal degrees to radians 
    lon1, lat1, lon2, lat2 = map(radians, [lon1, lat1, lon2, lat2])

    # haversine formula 
    dlon = lon2 - lon1 
    dlat = lat2 - lat1 
    a = sin(dlat/2)**2 + cos(lat1) * cos(lat2) * sin(dlon/2)**2
    c = 2 * asin(sqrt(a)) 
    r = 3958.8 # Radius of earth in kilometers. Use 3,958.8 for miles
    return c * r 


In [ ]:
distance = 0
for linestring in edge_masked.geometry[1:2]:
  line = [x for x in linestring.coords]
  numCoords = len(linestring.coords) - 1
  for i in range(0, numCoords):
    point1 = line[i]
    point2 = line[i + 1]
    distance += haversine(point1[1], point1[0], point2[1], point2[0])

distance * 5280

231.78167854000455

In [ ]:
distance

0.04389804517803116

In [ ]:
377/2

188.5

In [ ]:
np.sum(edges.length)

3.336694743488888